# Data Collecting

## Import libraries

In [1]:
import numpy as np
import pandas as pd 
import os
import fastf1 as f1

## Reading data

In [2]:
df_drivers = pd.read_csv('./archive/drivers.csv')
df_qualifying = pd.read_csv('./archive/qualifying.csv')
df_races = pd.read_csv('./archive/races.csv')
df_results = pd.read_csv('./archive/results.csv')
df_results_ = pd.read_csv('./archive/results.csv')
df_circuits = pd.read_csv('./archive/races.csv')

## Add data to final dataset

In [3]:
df_new = df_races.loc[:, ['raceId', 'date']].drop_duplicates(subset=['raceId'])
df_new = df_new.sort_values(by='date', key=lambda x: x.str.split('-'))
df_new['raceIdOrdered'] = range(1,len(df_new)+1)

df_results = pd.merge(df_results, df_new.loc[:, ['raceId', 'raceIdOrdered']], how='left', on=['raceId'], )
df_results = df_results.sort_values(by='raceIdOrdered')

df_results = df_results.set_index('raceId').join(df_races.loc[:,['year', 'raceId']].set_index('raceId'), on='raceId').reset_index()
df_results = df_results.loc[:,['raceId', 'driverId', 'grid', 'positionOrder', 'year', 'raceIdOrdered']]
df_results = df_results.rename(columns={'positionOrder' : 'racePosition', 'grid': 'startingPosition'})

min_year = df_results.groupby('driverId').min()['year']
min_year = (min_year.reset_index()).rename({'year':'yearStarted'}, axis=1)
df_results = df_results.merge(min_year, on='driverId',how='left')

df_results.head(10)

raceId  driverId  startingPosition  racePosition  year  raceIdOrdered  \
0     833       660                21            11  1950              1   
1     833       790                12            21  1950              1   
2     833       579                 3            12  1950              1   
3     833       661                10            20  1950              1   
4     833       789                 7            19  1950              1   
5     833       589                11            18  1950              1   
6     833       640                 8            17  1950              1   
7     833       785                17            16  1950              1   
8     833       747                18            15  1950              1   
9     833       778                20            10  1950              1   

   yearStarted  
0         1950  
1         1950  
2         1950  
3         1950  
4         1950  
5         1950  
6         1950  
7         1950  
8         1950  
9         1950

In [4]:
def get_race_experience(df):
    sol = []
    for index, row in df.iterrows():
        df_new = df.loc[:index]
        df_new = df_new[df_new['driverId'] == row['driverId']]
        sol.append(len(df_new))
    return sol
df_results['RacingExperience'] = get_race_experience(df_results)

In [5]:
df_results = df_results.merge(df_drivers.loc[:,['driverId', 'nationality']],how='left', on='driverId')

print(df_results[df_results['nationality'].isna()])
df_results.head(10)

Empty DataFrame
Columns: [raceId, driverId, startingPosition, racePosition, year, raceIdOrdered, yearStarted, RacingExperience, nationality]
Index: []


raceId  driverId  startingPosition  racePosition  year  raceIdOrdered  \
0     833       660                21            11  1950              1   
1     833       790                12            21  1950              1   
2     833       579                 3            12  1950              1   
3     833       661                10            20  1950              1   
4     833       789                 7            19  1950              1   
5     833       589                11            18  1950              1   
6     833       640                 8            17  1950              1   
7     833       785                17            16  1950              1   
8     833       747                18            15  1950              1   
9     833       778                20            10  1950              1   

   yearStarted  RacingExperience nationality  
0         1950                 1     Belgian  
1         1950                 1     British  
2         1950                 1   Argentine  
3         1950                 1     British  
4         1950                 1      French  
5         1950                 1  Monegasque  
6         1950                 1       Swiss  
7         1950                 1     British  
8         1950                 1     British  
9         1950                 1     British

## Removing data from final dataset

In [6]:
races_per_years = df_races['year'].value_counts()
race_ids_per_years = df_races.groupby('year')['raceId'].agg(list)
races_per_years = pd.concat([races_per_years, race_ids_per_years], axis=1).reset_index()
races_per_years.columns = ['Year', 'Total', 'RaceIds']
races_per_years = races_per_years.sort_values(by='Year')

In [7]:
data_for_races = df_results.loc[:,['raceId','year']].groupby('year').nunique()
data_expected = races_per_years.set_index('Year')['Total']
data_for_races = data_for_races.join(data_expected)
data_for_races['diff'] = data_for_races['Total'] - data_for_races['raceId']
data_for_races[data_for_races['diff'] != 0]

raceId  Total  diff
year                     
2023      12     22    10

In [8]:
years = df_races.loc[:,['year', 'raceId']].set_index('raceId')
df_qualifying = df_qualifying.set_index('raceId').join(years, on='raceId').reset_index()
print("First quali info: ", df_qualifying['year'].min())

First quali info:  1994


In [9]:
df_qualifying = df_qualifying[(df_qualifying['year'] >= 1996) & (df_qualifying['year'] <= 2022)]
df_qualifying = df_qualifying[(df_qualifying['year'] <= 2002) | (df_qualifying['year'] >= 2006)]

In [10]:
df_results = df_results[(df_results['year'] >= 1996) & (df_results['year'] <= 2022)]
df_results = df_results[(df_results['year'] <= 2002) | (df_results['year'] >= 2006)]

In [11]:
df_results = df_results[df_results['startingPosition'] != 0]

In [12]:
x = df_results['raceId'].unique()
y = df_qualifying['raceId'].unique()
np.where(np.isin(x, y) == False)

(array([  7,   8,   9,  10,  11,  12,  13,  14,  15,  26,  27,  28,  29,
         30,  31,  32,  36,  37,  38,  39,  40,  44,  46,  47,  48,  52,
         53,  54,  55,  56,  57,  58,  59,  60,  61,  62,  63,  64,  66,
         69,  70,  71,  72,  73,  74,  75,  76,  77,  78,  79,  81,  82,
         83,  84,  85,  86,  87,  88,  89,  90,  91,  92,  93,  94,  95,
         96,  98,  99, 101, 102, 103, 104, 105, 106, 107, 108, 109, 110,
        111, 112, 113, 114]),)

In [13]:
df_results = df_results[df_results['raceId'].isin(y)]
x = df_results['raceId'].unique()
print(np.where(np.isin(x, y) == False))

df = pd.merge(df_results, df_qualifying,  how='left', left_on=['raceId','driverId'], right_on = ['raceId','driverId'])
df = df.drop(['year_y', 'constructorId', 'qualifyId', 'number'], axis = 1)
df = df.rename(columns={'year_x' : 'year', 'position' : 'qualiResultPosition'})
df.head(10)

(array([], dtype=int64),)


raceId  driverId  startingPosition  racePosition  year  raceIdOrdered  \
0     224        21                16            14  1996            582   
1     224        85                22            22  1996            582   
2     224        69                21            21  1996            582   
3     224        65                14            20  1996            582   
4     224        84                19            19  1996            582   
5     224        55                 6            18  1996            582   
6     224        50                12            17  1996            582   
7     224        14                13            16  1996            582   
8     224        22                 8            15  1996            582   
9     224        30                 4            13  1996            582   

   yearStarted  RacingExperience nationality  qualiResultPosition        q1  \
0         1996                 1     Italian                 16.0  1:35.898   
1         1994                19     Italian                  NaN       NaN   
2         1993                32     Italian                  NaN       NaN   
3         1989                84     British                 14.0  1:35.453   
4         1984               150     British                 19.0  1:36.286   
5         1989               104      French                  6.0  1:34.257   
6         1994                16       Dutch                 12.0  1:35.338   
7         1994                26     British                 13.0  1:35.351   
8         1993                50   Brazilian                  8.0  1:34.474   
9         1991                70      German                  4.0  1:33.125   

    q2   q3  
0   \N   \N  
1  NaN  NaN  
2  NaN  NaN  
3   \N   \N  
4   \N   \N  
5   \N   \N  
6   \N   \N  
7   \N   \N  
8   \N   \N  
9   \N   \N

## Transform data 

In [14]:
df = df.replace('\\N', np.nan)
df = df[df['q1'].notnull()]
df = df.fillna(0)

In [15]:
def get_time_lst(df, col):
    col_lst = df[col].str.split(pat=':|\.').fillna(0)
    return col_lst

df['q1_lst'] = get_time_lst(df, 'q1')
df['q2_lst'] = get_time_lst(df, 'q2')
df['q3_lst'] = get_time_lst(df, 'q3')


In [16]:
def convert_to_msec(time_lst):
    if time_lst != 0:
        return int(time_lst[0])*60000 + int(time_lst[1])*1000 + int(time_lst[2])
    return 0

df['q1Msec'] = df.apply(lambda x: convert_to_msec(x['q1_lst']), axis=1)
df['q2Msec'] = df.apply(lambda x: convert_to_msec(x['q2_lst']), axis=1)
df['q3Msec'] = df.apply(lambda x: convert_to_msec(x['q3_lst']), axis=1)


df['maxPace'] = df.loc[:, ['q1Msec', 'q2Msec', 'q3Msec']].max(axis=1)
df['meanPace'] = df.loc[:, ['q1Msec', 'q2Msec', 'q3Msec']].sum(axis=1) / (df.loc[:, ['q1Msec', 'q2Msec', 'q3Msec']] != 0).sum(axis=1)

df = df.drop(['q1_lst', 'q2_lst', 'q3_lst', 'q1', 'q2', 'q3'], axis = 1)

df.head(10)

raceId  driverId  startingPosition  racePosition  year  raceIdOrdered  \
0      224        21                16            14  1996            582   
3      224        65                14            20  1996            582   
4      224        84                19            19  1996            582   
5      224        55                 6            18  1996            582   
6      224        50                12            17  1996            582   
7      224        14                13            16  1996            582   
8      224        22                 8            15  1996            582   
9      224        30                 4            13  1996            582   
10     224        44                11             7  1996            582   
11     224        79                15            11  1996            582   

    yearStarted  RacingExperience nationality  qualiResultPosition  q1Msec  \
0          1996                 1     Italian                 16.0   95898   
3          1989                84     British                 14.0   95453   
4          1984               150     British                 19.0   96286   
5          1989               104      French                  6.0   94257   
6          1994                16       Dutch                 12.0   95338   
7          1994                26     British                 13.0   95351   
8          1993                50   Brazilian                  8.0   94474   
9          1991                70      German                  4.0   93125   
10         1994                34      French                 11.0   95330   
11         1992                65    Japanese                 15.0   95715   

    q2Msec  q3Msec  maxPace  meanPace  
0        0       0    95898   95898.0  
3        0       0    95453   95453.0  
4        0       0    96286   96286.0  
5        0       0    94257   94257.0  
6        0       0    95338   95338.0  
7        0       0    95351   95351.0  
8        0       0    94474   94474.0  
9        0       0    93125   93125.0  
10       0       0    95330   95330.0  
11       0       0    95715   95715.0

In [17]:
df['driverExpYears'] = df['year'] - df['yearStarted']

In [18]:
idcircuits = []
for index, row in df.iterrows():
    idcircuits.append(df_races[df_races['raceId'] == row['raceId']]['circuitId'].tolist()[0])
df['circuitId'] = idcircuits
    

In [19]:
df

raceId  driverId  startingPosition  racePosition  year  raceIdOrdered  \
0        224        21                16            14  1996            582   
3        224        65                14            20  1996            582   
4        224        84                19            19  1996            582   
5        224        55                 6            18  1996            582   
6        224        50                12            17  1996            582   
...      ...       ...               ...           ...   ...            ...   
7679    1096        20                 9            10  2022           1079   
7680    1096       846                 7             6  2022           1079   
7681    1096       839                 8             7  2022           1079   
7682    1096       840                14             8  2022           1079   
7683    1096       847                 6             5  2022           1079   

      yearStarted  RacingExperience nationality  qualiResultPosition  q1Msec  \
0            1996                 1     Italian                 16.0   95898   
3            1989                84     British                 14.0   95453   
4            1984               150     British                 19.0   96286   
5            1989               104      French                  6.0   94257   
6            1994                16       Dutch                 12.0   95338   
...           ...               ...         ...                  ...     ...   
7679         2007               300      German                  9.0   85523   
7680         2019                82     British                  7.0   85387   
7681         2016               111      French                  8.0   85735   
7682         2017               122    Canadian                 14.0   85741   
7683         2019                82     British                  6.0   85545   

      q2Msec  q3Msec  maxPace      meanPace  driverExpYears  circuitId  
0          0       0    95898  95898.000000               0          1  
3          0       0    95453  95453.000000               7          1  
4          0       0    96286  96286.000000              12          1  
5          0       0    94257  94257.000000               7          1  
6          0       0    95338  95338.000000               2          1  
...      ...     ...      ...           ...             ...        ...  
7679   84974   84961    85523  85152.666667              15         24  
7680   84903   84769    85387  85019.666667               3         24  
7681   85007   84830    85735  85190.666667               6         24  
7682   85359       0    85741  85550.000000               5         24  
7683   84940   84511    85545  84998.666667               3         24  

[7590 rows x 17 columns]

In [20]:
df['raceId']

0        224
3        224
4        224
5        224
6        224
        ... 
7679    1096
7680    1096
7681    1096
7682    1096
7683    1096
Name: raceId, Length: 7590, dtype: int64

In [21]:
constructorId = []
for index, row in df.iterrows():
    condition = (df_results_['raceId'] == row['raceId']) & (df_results_['driverId'] == row['driverId'])
    constructorId.append(df_results_.loc[condition, 'constructorId'].tolist()[0])
    
df['constructorId'] = constructorId

# Add information about weather to dataset

In [22]:
columnAirTemp = []
columnHumidity = []
columnPressure = []
columnRainfall = []
columnTrackTemp = []
columnWindDirection = []
columnWindSpeed = []
for index, row in df.iterrows():
    try:
        condition = (df_circuits['raceId'] == row['raceId']) & (df_circuits['year'] == row['year'])
        session = f1.get_session(row['year'], df_circuits.loc[condition, 'name'].tolist()[0], 'Q')
        session.load(telemetry=False, laps=False, weather=True)
        columnAirTemp.append(session.weather_data['AirTemp'].mean())
        columnHumidity.append(session.weather_data['Humidity'].mean())
        columnPressure.append(session.weather_data['Pressure'].mean())
        columnRainfall.append(session.weather_data['Rainfall'].mean())
        columnTrackTemp.append(session.weather_data['TrackTemp'].mean())
        columnWindDirection.append(session.weather_data['WindDirection'].mean())
        columnWindSpeed.append(session.weather_data['WindSpeed'].mean())
    except:
        columnAirTemp.append(0)
        columnHumidity.append(0)
        columnPressure.append(0)
        columnRainfall.append(0)
        columnTrackTemp.append(0)
        columnWindDirection.append(0)
        columnWindSpeed.append(0)


req         WARNING 	DEFAULT CACHE ENABLED! (443.42 MB) /Users/olgafrolova/Library/Caches/fastf1
core           INFO 	Loading data for Australian Grand Prix - Qualifying [v3.2.1]
req            INFO 	No cached data found for session_info. Loading data...
_api           INFO 	Fetching session info data...
logger      WARNING 	Failed to load session info data!
core        WARNING 	Cannot load laps, telemetry, weather, and message data because the relevant API is not supported for this session.
core           INFO 	Finished loading data for 20 drivers: ['6', '5', '2', '1', '7', '3', '4', '11', '15', '19', '9', '17', '8', '14', '18', '21', '20', '16', '12', '10']
core           INFO 	Loading data for Australian Grand Prix - Qualifying [v3.2.1]
req            INFO 	No cached data found for session_info. Loading data...
_api           INFO 	Fetching session info data...
logger      WARNING 	Failed to load session info data!
core        WARNING 	Cannot load laps, telemetry, weather, and messa

In [23]:
df['AirTemp'] = columnAirTemp
df['Humidity'] = columnHumidity 
df['Pressure'] = columnPressure
df['Rainfall'] = columnRainfall 
df['TrackTemp'] = columnTrackTemp
df['WindDirection'] = columnWindDirection
df['WindSpeed'] = columnWindSpeed 

## Save final dataset

In [24]:
current_directory = os.getcwd()
parent_directory = os.path.dirname(current_directory)
os.chdir(parent_directory)

df.to_csv('f1dataset.csv', index=False)  